In [5]:
import time
import mujoco
import mujoco.viewer
import mediapy as media
import matplotlib.pyplot as plt
import numpy as np
import transforms3d.quaternions as quaternions
import copy
import os

In [6]:
cwd = os.path.dirname(os.getcwd())
path_guard = os.path.join(cwd,r"meshes\headGuard.stl")
path_platform = os.path.join(cwd,r"meshes\platform.stl")
print(cwd)
print(path_guard)
print(path_platform)
guard_obj = os.path.join(cwd,r"meshes\headGuard.obj")
#guard_obj = os.path.join(cwd,r"meshes\simpleBox.obj")

c:\Users\DGaard\Desktop\Gits\Master_MRI_Phantom\headSim
c:\Users\DGaard\Desktop\Gits\Master_MRI_Phantom\headSim\meshes\headGuard.stl
c:\Users\DGaard\Desktop\Gits\Master_MRI_Phantom\headSim\meshes\platform.stl


In [7]:
xml = f"""
<mujoco>
  <asset>
    <!-- WORLD -->
    <texture type="skybox" builtin="gradient" rgb1="0.3 0.5 0.7" rgb2="0 0 0" width="512" height="512" />
    <texture name="plane" type="2d" builtin="checker" rgb1=".2 .3 .4" rgb2=".1 0.15 0.2" width="512" height="512" mark="cross" markrgb=".8 .8 .8" />
    <material name="plane" reflectance="0.3" texture="plane" texrepeat="1 1" texuniform="true" />

    <!-- MESHES -->
    <mesh name="guard" file="{path_guard}"/>
    <mesh name="ywing" file="{path_platform}"/>
  </asset>


  <option>
    <!--flag contact="disable"/-->
    <!--flag gravity="disable"/-->
    <!--flag contact="disable" gravity="disable"/-->
  </option>
  <!--option  gravity="0 0 1"/-->


  <worldbody>
    <light directional="true" diffuse=".2 .2 .2" specular="0 0 0" pos="0 1 5" dir="0 -1 -1" castshadow="false"/>
    <light directional="false" diffuse=".8 .8 .8" specular="0.3 0.3 0.3" pos="0 -1 4" dir="0 0 -1" />
    <light directional="true" diffuse="0 0 0" specular=".7 .7 .7" pos="0 3 3" dir="0 -3 -3" />
    <geom name="floor" pos="0 0 0" group="1" size="0 0 .1" type="plane" material="plane" condim="3" />
    <camera name="fixed" pos="0.113 -4.286 5.167" xyaxes="1.000 0.003 0.000 -0.002 0.678 0.735"/>

    <body name="head" pos="0 0 1.5" euler="0 0 0">
        <joint name="freehead" type="free"/>
        <geom name="red_box" type="box" size="1 1 .2" rgba="1 0 0 1"/> !--add mass here if neeeded --
        <!--geom name="red_box" type="mesh" mesh="ywing"/-->

        <body name="rod11" pos="-1 -1 .3"> !-- change atatchment point to box -- 
              <joint name="ball11" type="ball" axis="1 0 0" pos="0 0 -.2"/>
              <geom name="rod11" type="capsule" size=".05 .2 .2" rgba="1 0 1 0.5"/>

              <body name="rod12" pos="0 0 .2" quat="1 0 0 0">
                <joint name="slide1" type="slide" axis="0 0 1" pos="0 0 0" limited="true" range="-.5 .5" damping="10000"/>
                <geom name="rod12" type="capsule" size=".05 .2 .2" rgba="1 1 0 0.5"/>

                <body name="anchor1" pos="0 0 .3">
                    <joint name="ball12" type="ball" axis="1 0 0" pos="0 0 -.1"/>
                    <geom name="anchor1" type="box" size=".1 .1 .1" rgba="0 0 1 1"/>
                </body>
              </body>
        </body>

        <body name="rod21" pos="1 1 .3"> !-- change atatchment point to box --
              <joint name="ball21" type="ball" axis="1 0 0" pos="0 0 -.2"/>
              <geom name="rod21" type="capsule" size=".05 .2 .2" rgba="1 0 1 0.5"/>

              <body name="rod22" pos="0 0 .2" quat="1 0 0 0">
                <joint name="slide2" type="slide" axis="0 0 1" pos="0 0 0" limited="true" range="-.5 .5" damping="10000"/>
                <geom name="rod22" type="capsule" size=".05 .2 .2" rgba="1 1 0 0.5"/>

                <body name="anchor2" pos="0 0 .3">
                    <joint name="ball22" type="ball" axis="1 0 0" pos="0 0 -.1"/>
                    <geom name="anchor2" type="box" size=".1 .1 .1" rgba="0 1 1 1"/>
                </body>
              </body>
        </body>

        <body name="rod31" pos="-1 0 .3"> !-- change atatchment point to box -- 
              <joint name="ball31" type="ball" axis="1 0 0" pos="0 0 -.2"/>
              <geom name="rod31" type="capsule" size=".05 .2 .2" rgba="1 0 1 0.5"/>

              <body name="rod32" pos="0 0 .2" quat="1 0 0 0">
                <joint name="slide3" type="slide" axis="0 0 1" pos="0 0 0" limited="true" range="-.5 .5" damping="10000"/>
                <geom name="rod32" type="capsule" size=".05 .2 .2" rgba="1 1 0 0.5"/>

                <body name="anchor3" pos="0 0 .3">
                    <joint name="ball32" type="ball" axis="1 0 0" pos="0 0 -.1"/>
                    <geom name="anchor3" type="box" size=".1 .1 .1" rgba="0 0 1 1"/>
                </body>
              </body>
        </body>

        <body name="rod41" pos="1 0 .3"> !-- change atatchment point to box --
              <joint name="ball41" type="ball" axis="1 0 0" pos="0 0 -.2"/>
              <geom name="rod41" type="capsule" size=".05 .2 .2" rgba="1 0 1 0.5"/>

              <body name="rod42" pos="0 0 .2" quat="1 0 0 0">
                <joint name="slide4" type="slide" axis="0 0 1" pos="0 0 0" limited="true" range="-.5 .5" damping="10000"/>
                <geom name="rod42" type="capsule" size=".05 .2 .2" rgba="1 1 0 0.5"/>

                <body name="anchor4" pos="0 0 .3">
                    <joint name="ball42" type="ball" axis="1 0 0" pos="0 0 -.1"/>
                    <geom name="anchor4" type="box" size=".1 .1 .1" rgba="0 1 1 1"/>
                </body>
              </body>
        </body>

        <body name="rod51" pos="-1 1 .3"> !-- change atatchment point to box -- 
              <joint name="ball51" type="ball" axis="1 0 0" pos="0 0 -.2"/>
              <geom name="rod51" type="capsule" size=".05 .2 .2" rgba="1 0 1 0.5"/>

              <body name="rod52" pos="0 0 .2" quat="1 0 0 0">
                <joint name="slide5" type="slide" axis="0 0 1" pos="0 0 0" limited="true" range="-.5 .5" damping="10000"/>
                <geom name="rod52" type="capsule" size=".05 .2 .2" rgba="1 1 0 0.5"/>

                <body name="anchor5" pos="0 0 .3">
                    <joint name="ball52" type="ball" axis="1 0 0" pos="0 0 -.1"/>
                    <geom name="anchor5" type="box" size=".1 .1 .1" rgba="0 0 1 1"/>
                </body>
              </body>
        </body>

        <body name="rod61" pos="1 -1 .3"> !-- change atatchment point to box --
              <joint name="ball61" type="ball" axis="1 0 0" pos="0 0 -.2"/>
              <geom name="rod61" type="capsule" size=".05 .2 .2" rgba="1 0 1 0.5"/>

              <body name="rod62" pos="0 0 .2" quat="1 0 0 0">
                <joint name="slide6" type="slide" axis="0 0 1" pos="0 0 0" limited="true" range="-.5 .5" damping="10000"/>
                <geom name="rod62" type="capsule" size=".05 .2 .2" rgba="1 1 0 0.5"/>

                <body name="anchor6" pos="0 0 .3">
                    <joint name="ball62" type="ball" axis="1 0 0" pos="0 0 -.1"/>
                    <geom name="anchor6" type="box" size=".1 .1 .1" rgba="0 1 1 1"/>
                </body>
              </body>
        </body>
    </body>

    <!--
    -->
    <body name="guard">
      <geom name="guard" type="mesh" mesh="guard" euler="0 -90 0"/>
    </body>
  </worldbody>

  <equality>
    !--change relpos to change the position of weld points  repective to the world--
    !-- torquescale="100" -- 

    <weld name = "anchor1" body1="anchor1" relpose="1 1 -2.3 1 0 0 0" torquescale="10000"/>
    <weld name = "anchor3" body1="anchor3" relpose="1 0 -2.3 1 0 0 0" torquescale="10000"/>


</mujoco>
"""

xml2 = """
<mujoco>
  <extension>
    <plugin plugin="mujoco.sdf.bowl">
      <instance name="bowl">
        <config key="height" value="0.4"/>
        <config key="radius" value="1.0"/>
        <config key="thickness" value="0.02"/>
      </instance>
    </plugin>
  </extension>

  <asset>
    <mesh name="bowl" file="{path_platform}">
      <plugin instance="bowl"/>
    </mesh>
     <!--mesh name="bowl"-->
       <!--plugin instance="bowl"/-->
     <!--/mesh-->
  </asset>

  <option sdf_iterations="5" sdf_initpoints="20"/>

  <default>
    <geom solref="0.01 1" solimp=".95 .99 .0001" condim="1"/>
  </default>

  <statistic meansize=".1"/>

  <!--include file="scene.xml"/-->

  <worldbody>
    <light name="left" pos="0 0 4"/>
    <light name="right" pos="-1 -1 2" dir="1 1 -2"/>
    <body euler="45 -15 0" pos="0 0 1">
      <geom type="sdf" name="bowl" mesh="bowl" rgba=".2 .8 .8 1">
        <plugin instance="bowl"/>
      </geom>
    </body>
    <body pos=".6 -.4 2.5">
      <freejoint/>
      <geom type="sphere" size=".15" rgba=".8 .17 .15 1"/>
    </body>
    <body pos="0 -.4 2.5">
      <freejoint/>
      <geom type="sphere" size=".15" rgba=".8 .17 .15 1"/>
    </body>
    <body pos=".3 -.4 2.5">
      <freejoint/>
      <geom type="sphere" size=".15" rgba=".8 .17 .15 1"/>
    </body>
  </worldbody>
</mujoco>"""

xml3 = f"""
<mujoco>
  <!--compiler texturedir="CollisionSdf/assets"/-->

  <extension>
    <plugin plugin="mujoco.sdf.sdflib">
      <instance name="sdf">
        <config key="aabb" value="0"/>
      </instance>
    </plugin>
  </extension>

  <asset>
    <!--texture name="texspot" type="2d" file="CollisionSdf/assets/spot.png"/-->
    <!--material name="matspot" texture="texspot"/-->
    <mesh name="spot" file="{guard_obj}">
      <plugin instance="sdf"/>
    </mesh>
  </asset>

  <option sdf_iterations="40" sdf_initpoints="100"/>

  <visual>
    <map force="1000"/>
  </visual>

  <default>
    <geom solref="0.01 1" solimp=".95 .99 .0001" friction="0.5"/>
  </default>

  <statistic meansize="0.2"/>

  <!--include file="scene.xml"/-->

  <worldbody>
    <body euler="90 0 0" pos="0 0 0">
      <geom type="sdf" name="cow1" mesh="spot" >
        <plugin instance="sdf"/>
      </geom>
    </body>

    <body pos="0 0 200">
      <freejoint/>
      <geom type="sdf" name="cow2" mesh="spot">
        <plugin instance="sdf"/>
      </geom>
    </body>

    <light name="left" pos="0 0 1"/>
    <light name="right" pos="1 0 1"/>
  </worldbody>
</mujoco>"""


model = mujoco.MjModel.from_xml_string(xml3)
data = mujoco.MjData(model)
mujoco.mj_kinematics(model,data)
#mujoco.viewer.launch(model)

In [8]:
with mujoco.viewer.launch_passive(model, data) as viewer:
  # Close the viewer automatically after 30 wall-seconds.
  start = time.time()
  while viewer.is_running() and time.time() - start < 3600:
    step_start = time.time()

    # mj_step can be replaced with code that also evaluates
    # a policy and applies a control signal before stepping the physics.
    mujoco.mj_step(model, data)

    # Example modification of a viewer option: toggle contact points every two seconds.
    with viewer.lock():
      viewer.opt.flags[mujoco.mjtVisFlag.mjVIS_CONTACTPOINT] = int(data.time % 2)
    
    # Pick up changes to the physics state, apply perturbations, update options from GUI.
    viewer.sync()


    # Rudimentary time keeping, will drift relative to wall clock.
    time_until_next_step = model.opt.timestep - (time.time() - step_start)
    print(time_until_next_step,time.time()-start)
    #if time_until_next_step > 0:
    # time.sleep(time_until_next_step)


0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.0010001659393310547
0.002 0.

: 